In [ ]:
import numpy as np
import scipy.linalg as spla
import scipy.integrate as spint
import scipy.sparse as sps
import scipy.sparse.linalg as spsla
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = [9., 6.]
plt.rcParams['font.size'] = 14.

# Linear parametric steady system - POD

Consider heat equation on a unit square:
$$
\begin{align*}
    -c(z_1, z_2) \Delta T(z_1, z_2) & = 1, \\
    T(z_1, 0) & = 1, \\
    T(z_1, 1) & = 0, \\
    T(0, z_2) & = 0, \\
    T(1, z_2) & = 0,
\end{align*}
$$
with $c(z_1, z_2) = \mu$ if $z_1, z_2 \in \left( \frac{1}{3}, \frac{2}{3} \right)$ and $c(z_1, z_2) = 1$ otherwise, and with output $y = \int_{(0, 1)^2} T(z_1, z_2) \, \mathrm{d}z$.

Discretize in each direction into $n + 2$ points and approximate $x_{ij}(\mu) \approx T(i h, j h)$, where $h = \frac{1}{n + 1}$, $i, j = 0, 1, 2, \ldots, n + 1$.

Then
$$
\begin{align*}
    -c_{ij} \frac{x_{i - 1, j} - 2 x_{ij} + x_{i + 1, j}}{h^2}
    - c_{ij} \frac{x_{i, j - 1} - 2 x_{ij} + x_{i, j + 1}}{h^2}
    = 1,
\end{align*}
$$
for $i, j = 1, 2, \ldots, n$.

For $j = 1$, we have $x_{i, j - 1} = 1$, so
$$
\begin{align*}
    -\frac{x_{i - 1, j} - 2 x_{ij} + x_{i + 1, j}}{h^2}
    - \frac{- 2 x_{ij} + x_{i, j + 1}}{h^2}
    = 1 + \frac{1}{h^2}.
\end{align*}
$$

We can rewrite this as
$$
\frac{1}{h^2} (L_1 + \mu L_2) X + \frac{1}{h^2} X (L_1^T + \mu L_2^T) = F.
$$

In [ ]:
k = 50
n = 3 * k - 2
h = 1 / (n + 1)

L1 = sps.diags([(k - 1) * [2] + k * [0] + (k - 1) * [2],
               (k - 2) * [-1] + k * [0] + (k - 1) * [-1],
               (k - 1) * [-1] + k * [0] + (k - 2) * [-1]],
              [0, -1, 1])
L2 = sps.diags([(k - 1) * [0] + k * [2] + (k - 1) * [0],
               (k - 2) * [0] + k * [-1] + (k - 1) * [0],
               (k - 1) * [0] + k * [-1] + (k - 2) * [0]],
              [0, -1, 1])

F = np.ones((n, n))
F[:, 0] += 1 / h**2

Vectorizing the equation, we get
$$\frac{1}{h^2} (I \otimes (L_1 + \mu L_2) + (L_1 + \mu L_2) \otimes I) x = f,$$
where $x$ and $f$ are vectorizations of $X$ and $F$.
Simplifying,
$$\frac{1}{h^2} (I \otimes L_1 + L_1 \otimes I + \mu (I \otimes L_2 + L_2 \otimes I)) x = f_1 + \frac{\mu}{h^2} f_2,$$

Let $A_1 = \frac{1}{h^2} (I \otimes L_1 + L_1 \otimes I)$, $A_2 = \frac{1}{h^2} (I \otimes L_2 + L_2 \otimes I)$, $B = f$. Then we have a system
$$
\begin{align*}
    (A1 + \mu A_2) x & = B, \\
    y & = C x,
\end{align*}
$$
with $C = \frac{1}{n^2} [1 \cdots 1]$.

In [ ]:
A1 = sps.kronsum(L1, L1) / h**2
A2 = sps.kronsum(L2, L2) / h**2
B = F.reshape((-1, 1), order='F')
C = np.ones((1, n**2)) / n**2

Let's see the solution for different $\mu$s.

In [ ]:
mu = 1

x = spsla.spsolve(A1 + mu * A2, B)

X = x.reshape((n, n), order='F')

X_full = np.zeros((n + 2, n + 2))
X_full[:, 0] = 1
X_full[1:-1, 1:-1] = X
X_full = np.rot90(X_full)

In [ ]:
plt.imshow(X_full)
plt.colorbar()
plt.show()

Let's plot the output of the system over $\mu \in [0.1, 10]$.

In [ ]:
#%%timeit
mus = np.logspace(-1, 1, 100)
ys = [C.dot(spsla.spsolve(A1 + mu * A2, B)) for mu in mus]

In [ ]:
plt.plot(mus, ys)
plt.show()

Here we do the reduction using POD.

In [ ]:
mu_train = np.logspace(-1, 1, 10)